<a href="https://colab.research.google.com/github/sholtodouglas/artificial_graphics/blob/main/train_jax_detr.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [2]:
!pip install pathy -q
!pip install wandb -q
!pip install flax -q 
!pip install jax-resnet -q
!pip install transformers -q
!pip install ray -q 

In [3]:
import tensorflow as tf

# You'll generate plots of attention in order to see which parts of an image
# your model focuses on during captioning
import matplotlib.pyplot as plt

import collections
import random
import numpy as np
import os
import time
import json
from PIL import Image


In [4]:
import requests
r = requests.get('https://ipinfo.io')
region = r.json()['region']
r.json()

{'city': 'Council Bluffs',
 'country': 'US',
 'hostname': '116.164.226.35.bc.googleusercontent.com',
 'ip': '35.226.164.116',
 'loc': '41.2619,-95.8608',
 'org': 'AS15169 Google LLC',
 'postal': '51502',
 'readme': 'https://ipinfo.io/missingauth',
 'region': 'Iowa',
 'timezone': 'America/Chicago'}

In [5]:
import argparse
from natsort import natsorted

parser = argparse.ArgumentParser(description='AG training arguments')
parser.add_argument('run_name')
parser.add_argument('--train_datasets', nargs='+', help='Training dataset names')
parser.add_argument('--val_datasets', nargs='+', help='Testing dataset names')
parser.add_argument('-c', '--colab', default=False, action='store_true', help='Enable if using colab environment')
parser.add_argument('-s', '--data_source', default='local', help='Source of training data')
parser.add_argument('-d', '--device', default='TPU', help='Hardware device to train on')
parser.add_argument('-b', '--batch_size', default=4, type=int)
parser.add_argument('-lr', '--learning_rate', type=float, default=1e-4)
parser.add_argument('-lr_bb', '--backbone_learning_rate', type=float, default=1e-5)
parser.add_argument('-t', '--train_steps', type=int, default=100000)
parser.add_argument('--bucket_name', help='GCS bucket name to stream data from')
parser.add_argument('--tpu_name', help='GCP TPU name') # Only used in the script on GCP

parser.add_argument('-dim', '--d_model', default=256, type=int)
parser.add_argument('-nh', '--num_heads', default=4, type=int)
parser.add_argument('-nl', '--num_layers', default=6, type=int)
parser.add_argument('-sl', '--sequence_length', default=128, type=int)
parser.add_argument('-dr', '--dropout_rate', type=float, default=0.1)
parser.add_argument('-cl', '--grad_clip_value', type=float, default=0.25)
parser.add_argument('-ds', '--distributed', type=bool, default=False)


### Sample local config
args = parser.parse_args('''
dummy_run2 
--train_datasets sample_data/custom/train
--val_datasets sample_data/custom/val
-c
--bucket_name artificial_graphics
'''.split())


In [6]:
from pathlib import Path
from pathy import Pathy
import os
import requests
import json
import pprint
import logging
import numpy as np
import tensorflow as tf
import time



pp = pprint.PrettyPrinter(indent=4)
# In[4]:


#@title Workpace Setup (Local vs Colab)

# Set up working directory and libraries
if args.colab:
    from google.colab import drive, auth
    print('Using colab setup')
    WORKING_PATH = Path('/content/artificial_graphics')
    # Clone repo
    try:
        get_ipython().system("git clone 'https://github.com/sholtodouglas/artificial_graphics' {WORKING_PATH}")
    except: 
        pass
    # Mount drive
    drive.mount('/content/drive')

    import jax.tools.colab_tpu
    jax.tools.colab_tpu.setup_tpu()
else:
    print('Using local setup')
    WORKING_PATH = Path.cwd()
    print(f'Working path: {WORKING_PATH}')

# Change working directory to artificial_graphics
os.chdir(WORKING_PATH)
import lib


if args.data_source == 'GCS':
    if args.colab:
      auth.authenticate_user()
    print('Reading data from Google Cloud Storage')
    r = requests.get('https://ipinfo.io')
    region = r.json()['region']
    project_id = 'learning-from-play-303306'
    logging.warning(f'You are accessing GCS data from {region}, make sure this is the same as your bucket {args.bucket_name}')
    STORAGE_PATH = Pathy(f'gs://{args.bucket_name}')
else:
    print('Reading data from local filesystem')
    STORAGE_PATH = WORKING_PATH

print(f'Storage path: {STORAGE_PATH}')
TRAIN_DATA_PATHS = [STORAGE_PATH/'data'/x for x in args.train_datasets]
VAL_DATA_PATHS = [STORAGE_PATH/'data'/x for x in args.val_datasets]

Using colab setup
fatal: destination path '/content/artificial_graphics' already exists and is not an empty directory.
Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
Reading data from local filesystem
Storage path: /content/artificial_graphics


In [8]:
!git pull
from importlib import reload
# reload(lib.DETR_jax)
# reload(lib.data)


Already up to date.


In [9]:
import jax
import flax
import flax.linen as nn
from jax import pmap
import jax.numpy as jnp
from jax import random
from dataclasses import dataclass
from typing import Dict, List, Optional, Tuple
from jax_resnet import pretrained_resnet, Sequential, slice_variables, ResNet50
from scipy.optimize import linear_sum_assignment
import lib.DETR_jax as lb
import torch # TODO once we remove the dataset dep
import optax

num_devices = len(jax.devices())

/usr/local/lib/python3.7/dist-packages/ray/autoscaler/_private/cli_logger.py:61: FutureWarning: Not all Ray CLI dependencies were found. In Ray 1.4+, the Ray CLI, autoscaler, and dashboard will only be usable via `pip install 'ray[default]'`. Please update your install command.
  "update your install command.", FutureWarning)


In [10]:
import ray
from ray.util import ActorPool
ray.init()

2021-08-02 14:57:16,260	INFO services.py:1247 -- View the Ray dashboard at http://127.0.0.1:8265


{'metrics_export_port': 65385,
 'node_id': '0de9c9f29b41104d56b5bf10a09c051e25a362f1833daf0e84547dc3',
 'node_ip_address': '172.28.0.2',
 'object_store_address': '/tmp/ray/session_2021-08-02_14-57-13_921570_1672129/sockets/plasma_store',
 'raylet_ip_address': '172.28.0.2',
 'raylet_socket_name': '/tmp/ray/session_2021-08-02_14-57-13_921570_1672129/sockets/raylet',
 'redis_address': '172.28.0.2:6379',
 'session_dir': '/tmp/ray/session_2021-08-02_14-57-13_921570_1672129',
 'webui_url': '127.0.0.1:8265'}

In [11]:
# Based on the class defined above, we create training and validation datasets.
#@title Data

from transformers import DetrFeatureExtractor
from lib.DETR import CocoDetection
feature_extractor = DetrFeatureExtractor.from_pretrained("facebook/detr-resnet-50")

feature_extractor.max_size = 512
feature_extractor.size = 256

train_dataset = CocoDetection(img_folder=f'{args.train_datasets[0]}', feature_extractor=feature_extractor)
val_dataset = CocoDetection(img_folder=f'{args.val_datasets[0]}', feature_extractor=feature_extractor, train=False)

from torch.utils.data import DataLoader

def collate_fn(batch):
  pixel_values = [item[0] for item in batch]
  encoding = feature_extractor.pad_and_create_pixel_mask(pixel_values, return_tensors="pt")
  labels = [item[1] for item in batch]
  batch = {}
  batch['pixel_values'] = encoding['pixel_values']
  batch['pixel_mask'] = encoding['pixel_mask']
  batch['labels'] = labels
  return batch


def to_jax(batch, num_devices=1):
    b = len(batch['pixel_values'])
    assert b % num_devices == 0 # if we're splitting it across devices, assert this
    batch['pixel_values'] = jnp.array(batch['pixel_values'].numpy().transpose(0,2,3,1))
    batch['pixel_mask'] = jnp.array(batch['pixel_mask'])
    batch['labels'] = [{k: jnp.array(v) for k,v in n.items()} for n in batch['labels']]
    
    indices =jnp.concatenate([jnp.arange(0,b, b//num_devices), jnp.array([b])])

    inputs = []
    for i in range(0, len(indices)-1):
        # inputs.append({k: v[indices[i]:indices[i+1]] for k,v in batch.items() if k != 'labels'})
        inputs.append(batch['pixel_values'][indices[i]:indices[i+1]])
    labels = []
    for i in range(0, len(indices)-1):
        labels.append(batch['labels'][indices[i]:indices[i+1]])
    return inputs, labels

train_dataloader = DataLoader(train_dataset, collate_fn=collate_fn, batch_size=16, drop_last=True, shuffle=True, num_workers = 3)
val_dataloader = DataLoader(val_dataset, collate_fn=collate_fn, batch_size=16, drop_last = True, shuffle=True, num_workers = 3)
cats = val_dataset.coco.cats
# Use this for the # classes
id2label = {k: v['name'] for k,v in cats.items()}

t_it = iter(train_dataloader)


loading annotations into memory...
Done (t=0.03s)
creating index...
index created!
loading annotations into memory...
Done (t=0.22s)
creating index...
index created!


In [12]:
@jax.jit
def func(params, inputs, rngs):
  out = model.apply(params, inputs, rngs = init_rngs)
  return out




In [13]:
inputs, labels = to_jax(next(t_it), num_devices=8)

In [14]:
# Initalise paramters and PRNGS
config = lb.TestConfig(output_dim=len(id2label))
rng = jax.random.PRNGKey(config.seed)
rng, init_rng = jax.random.split(rng)
dropout_rng = random.PRNGKey(1)
# create model
model = lb.DETR_transformer(config)
init_rngs = {'params': random.PRNGKey(0), 'dropout': dropout_rng}


In [60]:
params = model.init(init_rngs, inputs[0])
params = lb.load_pretrained_resnet(params)
adamw = optax.adamw(learning_rate=args.learning_rate)
opt_state = adamw.init(params)

In [15]:
# define loss functions and actor pool to distribute the non-jitable part out to cpus. 
matcher = lb.DetrHungarianMatcher()
loss = lb.DetrLoss(matcher, len(id2label), 0.2, ["labels", "boxes", "cardinality"])
actors =  ActorPool([lb.non_diff.remote(loss) for i in range(0,num_devices)])
# linear_decay_lr_schedule_fn = optax.linear_schedule(init_value=1e-4, end_value=0, transition_steps=100000)


In [61]:
# replicate params and PRNGs out to multiple TPUs
params = flax.jax_utils.replicate(params)
opt_state = flax.jax_utils.replicate(opt_state)
rng = jax.random.PRNGKey(42)
dropout_rngs = jax.random.split(rng, jax.local_device_count())

/usr/local/lib/python3.7/dist-packages/jax/lib/xla_bridge.py:387: UserWarning: jax.host_count has been renamed to jax.process_count. This alias will eventually be removed; please update your code.
  "jax.host_count has been renamed to jax.process_count. This alias "
/usr/local/lib/python3.7/dist-packages/jax/lib/xla_bridge.py:374: UserWarning: jax.host_id has been renamed to jax.process_index. This alias will eventually be removed; please update your code.
  "jax.host_id has been renamed to jax.process_index. This alias "


In [62]:
# create the optimizer


In [63]:
t_it = iter(train_dataloader)

In [64]:
def calc_loss(params, inputs, sorted_labels, rngs):
    outputs = func(params, inputs, rngs = rngs)
    losses, metrics = loss.get_losses(sorted_labels, outputs)
    return losses[0]

def get_grads(params, opt_state, inputs, sorted_labels, rngs):
    grad_fn = jax.value_and_grad(calc_loss)
    loss, grad = grad_fn(params, inputs, sorted_labels, rngs)
    grad = jax.lax.pmean(grad, "batch")
    
    updates, opt_state = adamw.update(grads, opt_state, params)
    params = optax.apply_updates(params, updates)
    return params, grad

In [65]:
def step(params, opt_state, inputs, labels):
  # convert from pytorch dataloader to jax (fine for the moment, as the labels are a funny format not much gain to be had from tf data pipeline)
  
  # model forward pass
  inputs = jnp.array(inputs)
  outputs = pmap(func, 'batch')(params, inputs, rngs = dropout_rngs)
  # take the outputs, partition into n devices
  no_grad_outputs = lb.partition_outputs(outputs, num_devices = num_devices)

  # using ray, split the matching process over n_devices cpus - FYI this should raise warnings about using CPU. It is 6x faster (from 8 devices) than doing it on tpu due to the retracing required. 

  tasks = [(no_grad_outputs[i], labels[i]) for i in range(num_devices)]
  sorted_labels = list(actors.map(lambda a, v: a.f.remote(v), tasks))
  sorted_labels = merge_arrangements(sorted_labels)

  grads = pmap(get_grads, 'batch')(params, opt_state, inputs, sorted_labels, dropout_rngs)

  return grads


def train_step(params, opt_state, batch):
  inputs, labels = to_jax(batch, num_devices=num_devices)
  params, grads = step(params, opt_state,  inputs, labels)
  # take_grads(arrangements, outputs)
  # grads = pmap(take_grads, 'batch')(arrangements, outputs)
  return params, grads


In [ ]:
grads = train_step(params, opt_state, t_it.next())

In [32]:
grads

{'batch_stats': {'backbone': FrozenDict({
      layers_0: {
          ConvBlock_0: {
              BatchNorm_0: {
                  mean: ShardedDeviceArray([[-0.02990374,  0.02284218, -0.0167001 , -0.02679213,
                                        0.01097122,  0.00518023,  0.01011879, -0.00032277,
                                        0.03107323, -0.02841784,  0.01209742, -0.03341291,
                                       -0.00759722, -0.01286783, -0.05163419, -0.06113204,
                                       -0.02222253, -0.01021221, -0.02312786,  0.01526006,
                                        0.01547507,  0.02251782, -0.06394155, -0.01123052,
                                       -0.04788939,  0.00073884, -0.01082688,  0.00383988,
                                       -0.02623885,  0.02984194, -0.00376716, -0.02752745,
                                       -0.02696774, -0.01627487, -0.10435916,  0.01741979,
                                        0.02707551, -0.048156

In [59]:
opt_state[0][1]['params']

{'backbone': FrozenDict({
     layers_0: {
         ConvBlock_0: {
             BatchNorm_0: {
                 bias: DeviceArray([[0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
                               0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
                               0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
                               0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
                               0., 0., 0., 0.],
                              [0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
                               0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
                               0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
                               0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
                               0., 0., 0., 0.],
                              [0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 

In [311]:
params['params']['backbone']['layers_0']['ConvBlock_0']['BatchNorm_0']['bias']

ShardedDeviceArray([[ 1.2902865 ,  0.8326036 ,  1.3563514 ,  1.3563491 ,
                      1.8570793 , -0.10893767,  0.5643446 ,  3.4863932 ,
                      0.6335926 ,  1.0452037 , -4.43668   ,  1.2039175 ,
                      1.2813013 ,  1.1248627 ,  1.1188178 ,  1.1835994 ,
                      0.95610875,  2.2098985 ,  1.017394  ,  0.8826757 ,
                      0.5134775 , -3.3208532 ,  1.2758178 ,  1.1750107 ,
                      1.304821  ,  0.86429346,  1.3614732 ,  1.1805242 ,
                      1.2972637 ,  0.9778689 ,  4.590446  ,  1.2872409 ,
                      0.7814426 ,  1.3816161 ,  1.229668  ,  1.5768201 ,
                      0.7743078 ,  1.359855  ,  1.4117426 ,  1.3524756 ,
                      1.5208088 ,  0.9607382 ,  0.73046434,  1.2747109 ,
                      1.3064505 ,  1.1343576 ,  1.1254011 , -2.3508122 ,
                      1.309785  ,  1.1138538 , -4.287662  ,  1.2744262 ,
                      1.3198553 ,  1.360717  ,  1.1

In [296]:
losses = step(t_it.next())

In [297]:
2*100000 / 60 / 60

55.55555555555556

In [266]:

tasks = [(no_grad_outputs[i], labels[i]) for i in range(num_devices)]
out = list(actors.map(lambda a, v: a.f.remote(v), tasks))

(pid=843284) 2021-08-02 11:32:15.505724: E external/org_tensorflow/tensorflow/stream_executor/cuda/cuda_driver.cc:271] failed call to cuInit: CUDA_ERROR_NO_DEVICE: no CUDA-capable device is detected
(pid=843284) WARNING:absl:No GPU/TPU found, falling back to CPU. (Set TF_CPP_MIN_LOG_LEVEL=0 and rerun for more info.)
(pid=843286) 2021-08-02 11:32:15.460156: E external/org_tensorflow/tensorflow/stream_executor/cuda/cuda_driver.cc:271] failed call to cuInit: CUDA_ERROR_NO_DEVICE: no CUDA-capable device is detected
(pid=843286) WARNING:absl:No GPU/TPU found, falling back to CPU. (Set TF_CPP_MIN_LOG_LEVEL=0 and rerun for more info.)
(pid=843278) 2021-08-02 11:32:15.435191: E external/org_tensorflow/tensorflow/stream_executor/cuda/cuda_driver.cc:271] failed call to cuInit: CUDA_ERROR_NO_DEVICE: no CUDA-capable device is detected
(pid=843278) WARNING:absl:No GPU/TPU found, falling back to CPU. (Set TF_CPP_MIN_LOG_LEVEL=0 and rerun for more info.)
(pid=843275) 2021-08-02 11:32:15.471031: E ext

In [22]:
def merge_arrangements(out):
    arrangements = {'ce_labels': [], 'box_loss_mask': [], 'target_boxes': [], 'num_boxes': [], 'cardinality_error': []}
    for arr in out:
        for k,v in arrangements.items():
            arrangements[k].append(arr[k])
    arrangements = {k: jnp.stack(v) for k,v in arrangements.items()}
    return arrangements
        

        

In [114]:
for i, o in enumerate(out):
  for t, (_, J) in zip(labels[i], o):
     print(t["class_labels"].shape,J)
  # 

(22,) [19 21  2 20 11 10 16 17  9  0  5  3  6  1  8 13 18  4 12 15 14  7]
(13,) [12  5 10  3  8  7  0  6  2  1 11  4  9]
(4,) [0 2 1 3]
(21,) [20  9 17 14  8  3 19 13 16  5 11  1  7  2 10 15  0 12  4  6 18]


In [270]:
losses

(ShardedDeviceArray([[ 9.5367985],
                     [ 8.148668 ],
                     [ 8.996886 ],
                     [10.36331  ],
                     [10.200222 ],
                     [ 8.260942 ],
                     [ 9.258766 ],
                     [ 9.79056  ]], dtype=float32),
 {'loss_ce': ShardedDeviceArray([3.1446514, 2.8827088, 3.4658241, 3.2817483, 2.9532793,
                      2.6226735, 3.177446 , 3.7480104], dtype=float32)},
 {'loss_bbox': ShardedDeviceArray([[0.7521363 ],
                      [0.5992607 ],
                      [0.62634367],
                      [0.8973181 ],
                      [0.90950584],
                      [0.7036856 ],
                      [0.73111945],
                      [0.70408994]], dtype=float32),
  'loss_giou': ShardedDeviceArray([[1.3157327],
                      [1.1348281],
                      [1.1996719],
                      [1.2974858],
                      [1.3497064],
                      [1.0599208],
 

In [11]:
from flax.training import train_state

In [ ]:
state = TrainState.create(
    apply_fn=model.apply,
    params=params,
    tx=adamw)
grad_fn = jax.grad(make_loss_fn(state.apply_fn))


In [ ]:
for batch in data:
  grads = grad_fn(state.params, batch)
  state = state.apply_gradients(grads=grads)

In [48]:
state = train_state.TrainState.create(apply_fn=model.__call__, params=params, tx=adamw)

In [ ]:
# on_device = jax.device_put(batch['pixel_values'], jax.devices()[0])


AttributeError: ignored

In [ ]:
dropout_rng, new_dropout_rng = jax.random.split(rng)

logits = state.apply_fn(inputs)[0]

AttributeError: ignored

In [ ]:
inputs = pmap(jax.device_put)(inputs)
params = flax.jax_utils.replicate(params)
rng = jax.random.PRNGKey(42)
dropout_rngs = jax.random.split(rng, jax.local_device_count())

/usr/local/lib/python3.7/dist-packages/jax/lib/xla_bridge.py:387: UserWarning: jax.host_count has been renamed to jax.process_count. This alias will eventually be removed; please update your code.
  "jax.host_count has been renamed to jax.process_count. This alias "
/usr/local/lib/python3.7/dist-packages/jax/lib/xla_bridge.py:374: UserWarning: jax.host_id has been renamed to jax.process_index. This alias will eventually be removed; please update your code.
  "jax.host_id has been renamed to jax.process_index. This alias "


In [ ]:
init_rngs = {'dropout': jax.random.split(rng, jax.local_device_count())}

In [ ]:
params['params'].keys()

dict_keys(['backbone', 'col_embed', 'feature_conv', 'linear_bbox', 'linear_class', 'queries', 'row_embed', 'transformer'])

In [ ]:
inputs2 = jnp.array(inputs)


In [ ]:
inputs2.shape

(8, 2, 256, 455, 3)

In [ ]:

outputs = pmap(model.apply)(params, inputs2, rngs = init_rngs)

In [ ]:
def to_jax(batch, num_devices=1):
    b = len(batch['pixel_values'])
    assert b % num_devices == 0 # if we're splitting it across devices, assert this
    batch['pixel_values'] = jnp.array(batch['pixel_values'].numpy().transpose(0,2,3,1))
    batch['pixel_mask'] = jnp.array(batch['pixel_mask'])
    batch['labels'] = [{k: jnp.array(v) for k,v in n.items()} for n in batch['labels']]
    
    indices =jnp.concatenate([jnp.arange(0,b, b//num_devices), jnp.array([b])])

    inputs = []
    for i in range(0, len(indices)-1):
        # inputs.append({k: v[indices[i]:indices[i+1]] for k,v in batch.items() if k != 'labels'})
        inputs.append(batch['pixel_values'][indices[i]:indices[i+1]])
    labels = []
    for i in range(0, len(indices)-1):
        labels.append(batch['labels'][indices[i]:indices[i+1]])
    return inputs, labels

In [ ]:
outputs['logits'].shape

(8, 2, 100, 16)

In [ ]:
for i,d in enumerate(jax.devices()):
  jax.device_put(labels[i], d)

AttributeError: ignored

In [ ]:
outputs = model.apply(params, inputs[0], rngs = init_rngs)

In [ ]:
def train_step(state, batch, dropout_rng):
    dropout_rng, new_dropout_rng = jax.random.split(dropout_rng)

    def loss_fn(params):
        labels = batch.pop("labels")

        logits = state.apply_fn(**batch, params=params, dropout_rng=dropout_rng, train=True)[0]

        # compute loss, ignore padded input tokens
        label_mask = jax.numpy.where(labels > 0, 1.0, 0.0)
        loss = optax.softmax_cross_entropy(logits, onehot(labels, logits.shape[-1])) * label_mask

        # take average
        loss = loss.sum() / label_mask.sum()

        return loss

    grad_fn = jax.value_and_grad(loss_fn)
    loss, grad = grad_fn(state.params)
    grad = jax.lax.pmean(grad, "batch")
    new_state = state.apply_gradients(grads=grad)

    metrics = jax.lax.pmean(
        {"loss": loss, "learning_rate": linear_decay_lr_schedule_fn(state.step)}, axis_name="batch"
    )

    return new_state, metrics, new_dropout_rng

8

In [ ]:
outputs = pmap(model.apply)(params, inputs, rngs = init_rngs)

AssertionError: ignored

In [ ]:

    
matcher = lb.DetrHungarianMatcher()
loss = lb.DetrLoss(matcher, len(id2label), 0.2, ["labels", "boxes", "cardinality"])
loss.forward(outputs, batch['labels'])

(DeviceArray([5.8699837], dtype=float32),
 {'cardinality_error': DeviceArray(61.5, dtype=float32),
  'loss_bbox': DeviceArray([0.6418719], dtype=float32),
  'loss_ce': DeviceArray(4.0058007, dtype=float32),
  'loss_giou': DeviceArray([1.2223113], dtype=float32)})

In [ ]:
for k,v in batch.items():
  try:
    print(k,v.shape)
  except:
    print(k, len(v))


pixel_values (16, 256, 455, 3)
pixel_mask (16, 256, 455)
labels 16


In [ ]:
import time
t0 = time.time()
t_it.next()
print(time.time()-t0)

StopIteration: ignored

In [ ]:
batch

{'labels': [{'area': DeviceArray([48811.684  , 19418.396  ,   380.5267 ,  3286.3704 ,
                 2680.985  ,  2680.985  ,   380.5267 ,  3286.3704 ,
                 2680.985  ,  2680.985  ,    73.03561,    73.03561,
                  174.0422 ,   380.5267 ,  3286.3704 ,  2680.985  ,
                 2680.985  ,    96.14334,   174.0422 ,   400.04663,
                  888.666  ,   646.5666 ,   478.13132,  3296.2124 ,
                 4110.0537 ,  1164.8    ,  1164.8    ], dtype=float32),
   'boxes': DeviceArray([[0.60995156, 0.5806387 , 0.6708738 , 0.6246426 ],
                [0.5       , 0.14988428, 0.8625    , 0.1932871 ],
                [0.6021259 , 0.2987346 , 0.06066164, 0.0538542 ],
                [0.6545156 , 0.43891302, 0.1654411 , 0.17053825],
                [0.6545156 , 0.7605027 , 0.1654411 , 0.13912314],
                [0.6545156 , 0.6011905 , 0.1654411 , 0.1391232 ],
                [0.41538316, 0.2987346 , 0.06066164, 0.0538542 ],
                [0.4677729 , 0.

## Initialize InceptionV3 and load the pretrained Imagenet weights

Now you'll create a tf.keras model where the output layer is the last convolutional layer in the InceptionV3 architecture. The shape of the output of this layer is ```8x8x2048```. You use the last convolutional layer because you are using attention in this example. You don't perform this initialization during training because it could become a bottleneck.

* You forward each image through the network and store the resulting vector in a dictionary (image_name --> feature_vector).
* After all the images are passed through the network, you save the dictionary to disk.


In [ ]:
image_model = tf.keras.applications.InceptionV3(include_top=False,
                                                weights='imagenet')
new_input = image_model.input
hidden_layer = image_model.layers[-1].output

image_features_extract_model = tf.keras.Model(new_input, hidden_layer)

Your images and captions are ready! Next, let's create a `tf.data` dataset to use for training your model.

In [ ]:
# Feel free to change these parameters according to your system's configuration

BUFFER_SIZE = 1000
embedding_dim = 256
units = 512
vocab_size = 6 # TODO Change
num_steps = 10000
# Shape of the vector extracted from InceptionV3 is (64, 2048)
# These two variables represent that vector shape
features_shape = 2048
attention_features_shape = 64

## Model

Fun fact: the decoder below is identical to the one in the example for [Neural Machine Translation with Attention](../sequences/nmt_with_attention.ipynb).

The model architecture is inspired by the [Show, Attend and Tell](https://arxiv.org/pdf/1502.03044.pdf) paper.

* In this example, you extract the features from the lower convolutional layer of InceptionV3 giving us a vector of shape (8, 8, 2048).
* You squash that to a shape of (64, 2048).
* This vector is then passed through the CNN Encoder (which consists of a single Fully connected layer).
* The RNN (here GRU) attends over the image to predict the next word.

In [ ]:
class BahdanauAttention(tf.keras.Model):
  def __init__(self, units):
    super(BahdanauAttention, self).__init__()
    self.W1 = tf.keras.layers.Dense(units)
    self.W2 = tf.keras.layers.Dense(units)
    self.V = tf.keras.layers.Dense(1)

  def call(self, features, hidden):
    # features(CNN_encoder output) shape == (batch_size, 64, embedding_dim)

    # hidden shape == (batch_size, hidden_size)
    # hidden_with_time_axis shape == (batch_size, 1, hidden_size)
    hidden_with_time_axis = tf.expand_dims(hidden, 1)

    # attention_hidden_layer shape == (batch_size, 64, units)
    attention_hidden_layer = (tf.nn.tanh(self.W1(features) +
                                         self.W2(hidden_with_time_axis)))

    # score shape == (batch_size, 64, 1)
    # This gives you an unnormalized score for each image feature.
    score = self.V(attention_hidden_layer)

    # attention_weights shape == (batch_size, 64, 1)
    attention_weights = tf.nn.softmax(score, axis=1)

    # context_vector shape after sum == (batch_size, hidden_size)
    context_vector = attention_weights * features
    context_vector = tf.reduce_sum(context_vector, axis=1)

    return context_vector, attention_weights

In [ ]:
class CNN_Encoder(tf.keras.Model):
    # Since you have already extracted the features and dumped it
    # This encoder passes those features through a Fully connected layer
    def __init__(self, embedding_dim):
        super(CNN_Encoder, self).__init__()
        # shape after fc == (batch_size, 64, embedding_dim)
        self.fc = tf.keras.layers.Dense(embedding_dim)

    def call(self, x):
        x = self.fc(x)
        x = tf.nn.relu(x)
        return x

In [ ]:
class RNN_Decoder(tf.keras.Model):
  def __init__(self, embedding_dim, units, vocab_size):
    super(RNN_Decoder, self).__init__()
    self.units = units

    self.embedding = tf.keras.layers.Embedding(vocab_size, embedding_dim)
    self.gru = tf.keras.layers.GRU(self.units,
                                   return_sequences=True,
                                   return_state=True,
                                   recurrent_initializer='glorot_uniform')
    self.fc1 = tf.keras.layers.Dense(self.units)
    self.fc2 = tf.keras.layers.Dense(vocab_size)

    self.attention = BahdanauAttention(self.units)

  def call(self, x, features, hidden):
    # defining attention as a separate model
    context_vector, attention_weights = self.attention(features, hidden)

    # x shape after passing through embedding == (batch_size, 1, embedding_dim)
    x = self.embedding(x)

    # x shape after concatenation == (batch_size, 1, embedding_dim + hidden_size)
    x = tf.concat([tf.expand_dims(context_vector, 1), x], axis=-1)

    # passing the concatenated vector to the GRU
    output, state = self.gru(x)

    # shape == (batch_size, max_length, hidden_size)
    x = self.fc1(output)

    # x shape == (batch_size * max_length, hidden_size)
    x = tf.reshape(x, (-1, x.shape[2]))

    # output shape == (batch_size * max_length, vocab)
    x = self.fc2(x)

    return x, state, attention_weights

  def reset_state(self, batch_size):
    return tf.zeros((batch_size, self.units))

In [ ]:
encoder = CNN_Encoder(embedding_dim)
decoder = RNN_Decoder(embedding_dim, units, vocab_size)

In [ ]:
optimizer = tf.keras.optimizers.Adam()
loss_object = tf.keras.losses.SparseCategoricalCrossentropy(
    from_logits=True, reduction='none')


def loss_function(real, pred):
  mask = tf.math.logical_not(tf.math.equal(real, 0))
  loss_ = loss_object(real, pred)

  mask = tf.cast(mask, dtype=loss_.dtype)
  loss_ *= mask

  return tf.reduce_mean(loss_)

## Checkpoint

In [ ]:
import wandb
wandb.init(project="artificial_graphics")
wandb.run.name = args.run_name
t = 0

wandb: Currently logged in as: sholto (use `wandb login --relogin` to force relogin)


In [ ]:
checkpoint_path = str(STORAGE_PATH/f'saved_models/{args.run_name}')
ckpt = tf.train.Checkpoint(encoder=encoder,
                           decoder=decoder,
                           optimizer=optimizer)
ckpt_manager = tf.train.CheckpointManager(ckpt, checkpoint_path, max_to_keep=5)

In [ ]:
start_epoch = 0
if ckpt_manager.latest_checkpoint:
  start_epoch = int(ckpt_manager.latest_checkpoint.split('-')[-1])
  # restoring the latest checkpoint in checkpoint_path
  ckpt.restore(ckpt_manager.latest_checkpoint)

## Training

* You extract the features stored in the respective `.npy` files and then pass those features through the encoder.
* The encoder output, hidden state(initialized to 0) and the decoder input (which is the start token) is passed to the decoder.
* The decoder returns the predictions and the decoder hidden state.
* The decoder hidden state is then passed back into the model and the predictions are used to calculate the loss.
* Use teacher forcing to decide the next input to the decoder.
* Teacher forcing is the technique where the target word is passed as the next input to the decoder.
* The final step is to calculate the gradients and apply it to the optimizer and backpropagate.


In [ ]:
def accuracy(real, pred):
  
  padding = tf.cast(real != 0, tf.float32)
  pred = tf.cast(tf.squeeze(tf.random.categorical(pred, 1)), tf.int32)
  # print(padding*pred, padding)
  
  correct = tf.cast(real == pred, tf.float32)
  return tf.reduce_sum(correct*padding) / tf.reduce_sum(padding) # multiply by padding to 0 out anything which is a pad and then divide by it to get dividue by non pads e.g ./5


@tf.function
def train_step(img_tensor, target):
  loss = 0

  # initializing the hidden state for each batch
  # because the captions are not related from image to image
  hidden = decoder.reset_state(batch_size=target.shape[0])

  dec_input = tf.expand_dims([1] * target.shape[0], 1)

  img_features = image_features_extract_model(img_tensor)
  img_features = tf.reshape(img_features, (img_features.shape[0], -1, img_features.shape[3]))

  metrics = {}
  with tf.GradientTape() as tape:
      features = encoder(img_features)

      for i in range(0, target.shape[1]):
          # passing the features through the decoder
          predictions, hidden, _ = decoder(dec_input, features, hidden)

          loss += loss_function(target[:, i], predictions)
          metrics[f"train_acc_step_{i}"] =  accuracy(target[:,i], predictions)
          
          # using teacher forcing
          dec_input = tf.expand_dims(target[:, i], 1)


  trainable_variables = encoder.trainable_variables + decoder.trainable_variables

  gradients = tape.gradient(loss, trainable_variables)

  optimizer.apply_gradients(zip(gradients, trainable_variables))


  metrics['train_loss'] =  (loss / int(target.shape[1]))


  return metrics

@tf.function
def step(img_tensor, target):
  loss = 0

  # initializing the hidden state for each batch
  # because the captions are not related from image to image
  hidden = decoder.reset_state(batch_size=target.shape[0])

  dec_input = tf.expand_dims([1] * target.shape[0], 1)

  img_features = image_features_extract_model(img_tensor)
  img_features = tf.reshape(img_features, (img_features.shape[0], -1, img_features.shape[3]))


  features = encoder(img_features)
  metrics = {}
  for i in range(0, target.shape[1]):
      # passing the features through the decoder
      predictions, hidden, _ = decoder(dec_input, features, hidden)

      loss += loss_function(target[:, i], predictions)
      metrics[f"test_acc_step_{i}"] =  accuracy(target[:,i], predictions)
      # using teacher forcing
      dec_input = tf.expand_dims(target[:, i], 1)


  metrics['test_loss'] =  loss / int(target.shape[1])
  return metrics


In [ ]:
# data = train_dataset.next()
# metrics = train_step(data['img'], data['target'])

In [ ]:

for data in train_dataset:
    train_metrics = train_step(data['img'], data['target'])

    if t % 100 == 0:
        test_data = test_dataset.next()
        test_metrics = step(test_data['img'], test_data['target'])
        print(f'Batch {t} Loss {train_metrics["train_loss"]:.4f} Valid loss {test_metrics["test_loss"]:.4f}')
        wandb.log(train_metrics, step=t)
        wandb.log(test_metrics, step=t)
    if t % 1000 == 0:
      ckpt_manager.save()
    t += 1


Batch 0 Loss 0.9647 Valid loss 0.7970
Batch 100 Loss 0.2871 Valid loss 0.5000
Batch 200 Loss 0.1882 Valid loss 0.2239
Batch 300 Loss 0.1602 Valid loss 0.0964
Batch 400 Loss 0.1267 Valid loss 0.0676
Batch 500 Loss 0.1702 Valid loss 0.0366
Batch 600 Loss 0.0227 Valid loss 0.0993
Batch 700 Loss 0.0404 Valid loss 0.0000
Batch 800 Loss 0.0057 Valid loss 0.0136
Batch 900 Loss 0.1917 Valid loss 0.0883
Batch 1000 Loss 0.0037 Valid loss 0.0911
Batch 1100 Loss 0.0465 Valid loss 0.0007
Batch 1200 Loss 0.0074 Valid loss 0.0011
Batch 1300 Loss 0.0291 Valid loss 0.0157
Batch 1400 Loss 0.0011 Valid loss 0.0164
Batch 1500 Loss 0.0235 Valid loss 0.0007
Batch 1600 Loss 0.0160 Valid loss 0.0120
Batch 1700 Loss 0.0004 Valid loss 0.0003
Batch 1800 Loss 0.0007 Valid loss 0.0359
Batch 1900 Loss 0.0005 Valid loss 0.0097
Batch 2000 Loss 0.0209 Valid loss 0.0012
Batch 2100 Loss 0.0047 Valid loss 0.0063
Batch 2200 Loss 0.0008 Valid loss 0.0008


KeyboardInterrupt: ignored

## Caption!

* The evaluate function is similar to the training loop, except you don't use teacher forcing here. The input to the decoder at each time step is its previous predictions along with the hidden state and the encoder output.
* Stop predicting when the model predicts the end token.
* And store the attention weights for every time step.

In [ ]:
shapes = { 2: '<end>', 
      3: 'Rectangle',
       4: 'Chevron',
        5: 'Oval'}

In [ ]:
data = train_dataset.next()
max_length = data['target'].shape[1]
def evaluate(image):
    attention_plot = np.zeros((max_length, attention_features_shape))

    hidden = decoder.reset_state(batch_size=1)

    temp_input = tf.expand_dims(image, 0)
    img_tensor_val = image_features_extract_model(temp_input)
    img_tensor_val = tf.reshape(img_tensor_val, (img_tensor_val.shape[0],
                                                 -1,
                                                 img_tensor_val.shape[3]))

    features = encoder(img_tensor_val)

    dec_input = tf.expand_dims([1], 0)
    result = []

    for i in range(max_length):
        predictions, hidden, attention_weights = decoder(dec_input,
                                                         features,
                                                         hidden)

        attention_plot[i] = tf.reshape(attention_weights, (-1, )).numpy()

        predicted_id = tf.random.categorical(predictions, 1)[0][0].numpy()
        result.append(shapes[predicted_id])

        if predicted_id == 2:
            return result, attention_plot

        dec_input = tf.expand_dims([predicted_id], 0)

    attention_plot = attention_plot[:len(result), :]
    return result, attention_plot

In [ ]:
def plot_attention(img, result, attention_plot):
    temp_image = np.array(img)

    fig = plt.figure(figsize=(10, 10))

    len_result = len(result)
    for i in range(len_result):
        temp_att = np.resize(attention_plot[i], (8, 8))
        grid_size = max(np.ceil(len_result/2), 2)
        ax = fig.add_subplot(grid_size, grid_size, i+1)
        ax.set_title(result[i])
        img = ax.imshow(temp_image)
        ax.imshow(temp_att, cmap='gray', alpha=0.6, extent=img.get_extent())

    plt.tight_layout()
    plt.show()

In [ ]:
data = test_dataset.next()
image = data['img'][0]
plt.imshow(image)

In [ ]:
# captions on the validation set

# real_caption = ' '.join([tokenizer.index_word[i]
#                         for i in cap_val[rid] if i not in [0]])
result, attention_plot = evaluate(image)

# print('Real Caption:', real_caption)
print('Prediction Caption:', ' '.join(result))
plot_attention(image, result, attention_plot)

Prediction Caption: Rectangle Chevron Rectangle <end>


## Try it on your own images

For fun, below you're provided a method you can use to caption your own images with the model you've just trained. Keep in mind, it was trained on a relatively small amount of data, and your images may be different from the training data (so be prepared for weird results!)


In [ ]:
image_url = 'https://tensorflow.org/images/surf.jpg'
image_extension = image_url[-4:]
image_path = tf.keras.utils.get_file('image'+image_extension, origin=image_url)

result, attention_plot = evaluate(image_path)
print('Prediction Caption:', ' '.join(result))
plot_attention(image_path, result, attention_plot)
# opening the image
Image.open(image_path)

# Next steps

Congrats! You've just trained an image captioning model with attention. Next, take a look at this example [Neural Machine Translation with Attention](../sequences/nmt_with_attention.ipynb). It uses a similar architecture to translate between Spanish and English sentences. You can also experiment with training the code in this notebook on a different dataset.